# Running Tensorflow on a GPU on Pin

In [13]:
# Import tensorflow and check version
import tensorflow as tf
print('Tensorflow version is', tf.__version__)

Tensorflow version is 2.2.0


## Looking at the GPUs

In [14]:
# List Available GPUs
gpus = tf.config.experimental.list_physical_devices('GPU')
for g in gpus:
    print(g)

PhysicalDevice(name='/physical_device:GPU:0', device_type='GPU')
PhysicalDevice(name='/physical_device:GPU:1', device_type='GPU')
PhysicalDevice(name='/physical_device:GPU:2', device_type='GPU')
PhysicalDevice(name='/physical_device:GPU:3', device_type='GPU')


## List the current processes running on the GPUs
Note that you can open a new terminal from the Jupyter Hub home page `New->Terminal` and type `nvidia-smi` to see the same results. Do this to see the process that this page is running, as you can only run one notebook cell at a time. 

In [38]:
# Display the processes currently running on the GPUs

import subprocess
n = str(subprocess.check_output(["nvidia-smi"]))
n = n.replace("\\n", "\n")
print(n)

b'Tue Jul 14 14:19:25 2020       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 440.59       Driver Version: 440.59       CUDA Version: 10.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|===============================+======================+======================|
|   0  GeForce GTX 108...  Off  | 00000000:18:00.0 Off |                  N/A |
|  0%   19C    P8    11W / 280W |  11060MiB / 11178MiB |      0%      Default |
+-------------------------------+----------------------+----------------------+
|   1  GeForce GTX 108...  Off  | 00000000:3B:00.0 Off |                  N/A |
|  0%   18C    P8    11W / 280W |  10670MiB / 11178MiB |      0%      Default |
+-------------------------------+----------------------+----------------------+
|   2 

## Working with Tensorflow
The following bit of code uses Keras, which is built into Tensorflow 2, to build a simple MLP to learn from some random data.

Points to note:
- `os.environ['TF_FORCE_GPU_ALLOW_GROWTH'] = 'true'` is important - it avoids fillinf the GPU memory
- `with tf.device('/GPU:3'):` tells the code to use GPU 3. Use `nvidia-smi` as described above to see which GPU has least load when you start.
- The training data inputs and outputs should be numpy arrays. You will want to read your own data here. Check out one of the image processing notebooks for more details.

In [39]:
# Limit memory usage for GPU
import os
os.environ['TF_FORCE_GPU_ALLOW_GROWTH'] = 'true'

from tensorflow.keras import Sequential
from tensorflow.keras.layers import Dense
import numpy as np

# Random input data - replace this with your data
x = np.random.random((1000,10))
# Random output data
y = np.random.random(1000)

with tf.device('/GPU:3'):
    model = Sequential()
    # Add a single hidden layer of 20 nodes, connected to 10 inputs
    model.add(Dense(20, input_shape=(10,)))
    # Add single node output layer
    model.add(Dense(1))
    model.compile(optimizer='adam', loss='MeanSquaredError', metrics=['accuracy'])
    # fit the model
    model.fit(x, y, epochs=150, batch_size=32, verbose=0)